In [7]:
import requests
import pandas as pd
from datetime import datetime, timedelta

# --- PASTE YOUR *PRODUCTION* CLIENT ID (APP ID) HERE ---
# You only need this one key for the Finding API.
CLIENT_ID_PRODUCTION = 

def find_sold_items(keyword):
    """
    Uses the simple and reliable Finding API to get sold listings.
    This does NOT use OAuth tokens.
    """
    print(f"Searching for SOLD items using the Finding API for: '{keyword}'")
    
    url = "https://svcs.ebay.com/services/search/FindingService/v1"
    
    headers = {
        "X-EBAY-SOA-SECURITY-APPNAME": CLIENT_ID_PRODUCTION,
        "X-EBAY-SOA-RESPONSE-DATA-FORMAT": "JSON",
        "X-EBAY-SOA-OPERATION-NAME": "findCompletedItems",
    }
    
    params = {
        "keywords": keyword,
        "itemFilter(0).name": "SoldItemsOnly",
        "itemFilter(0).value": "true",
        "sortOrder": "EndTimeSoonest",
        "paginationInput.entriesPerPage": 100,
    }
    
    response = requests.get(url, headers=headers, params=params)
    response.raise_for_status() # Will stop if there's an error
    
    print("   SUCCESS! Data received from the Finding API.")
    return response.json()

# --- Main Program ---
try:
    product_to_research = "Macbook Air M1"
    
    # Execute the function to get the data
    data = find_sold_items(product_to_research)
    
    # The structure of the response is different, so we process it differently
    results = data['findCompletedItemsResponse'][0]['searchResult'][0].get('item', [])
    
    if results:
        items_list = []
        for item in results:
            item_details = {
                'title': item.get('title', [None])[0],
                'price': float(item['sellingStatus'][0]['currentPrice'][0]['__value__']),
                'currency': item['sellingStatus'][0]['currentPrice'][0]['@currencyId'],
                'condition': item.get('condition', [{}])[0].get('conditionDisplayName', [None])[0],
                'end_time': item.get('listingInfo', [{}])[0].get('endTime', [None])[0],
                'item_url': item.get('viewItemURL', [None])[0]
            }
            items_list.append(item_details)
        
        # Create the DataFrame
        df = pd.DataFrame(items_list)
        
        print(f"\nCreated a DataFrame with {len(df)} sales records.")
        
        # Now you can use this DataFrame 'df' for your analysis in other cells
        
    else:
        print(f"\nNo sold listings found for '{product_to_research}'.")
        df = pd.DataFrame()

except Exception as e:
    print("\n--- AN ERROR OCCURRED ---")
    print(e)

Searching for SOLD items using the Finding API for: 'Macbook Air M1'

--- AN ERROR OCCURRED ---
500 Server Error: Internal Server Error for url: https://svcs.ebay.com/services/search/FindingService/v1?keywords=Macbook+Air+M1&itemFilter%280%29.name=SoldItemsOnly&itemFilter%280%29.value=true&sortOrder=EndTimeSoonest&paginationInput.entriesPerPage=100


In [8]:
import requests
import base64
import pandas as pd
import json

# --- PASTE YOUR ACTIVE PRODUCTION KEYS HERE ---
CLIENT_ID_PRODUCTION = "Kamalpre-retailpr-PRD-f8e8dd193-b0972a73"
CLIENT_SECRET_PRODUCTION = "PRD-8e8dd193d73f-b8d1-4bad-a5ca-ec24"

def get_browse_api_token():
    """Gets the simple token needed for the Browse API."""
    print("1. Getting the correct access token...")
    url = "https://api.ebay.com/identity/v1/oauth2/token" 
    headers = {
        "Content-Type": "application/x-www-form-urlencoded",
        "Authorization": "Basic " + base64.b64encode(f"{CLIENT_ID_PRODUCTION}:{CLIENT_SECRET_PRODUCTION}".encode()).decode()
    }
    # This is the simple scope that we know works.
    body = {
        "grant_type": "client_credentials",
        "scope": "https://api.ebay.com/oauth/api_scope"
    }
    response = requests.post(url, headers=headers, data=body)
    response.raise_for_status() 
    print("   SUCCESS! Token obtained.")
    return response.json()["access_token"]

def find_active_items(access_token, keyword, limit=100):
    """
    Uses the Browse API to find CURRENTLY ACTIVE listings.
    This is the API that is available to you.
    """
    print(f"\n2. Searching for ACTIVE listings for: '{keyword}'...")
    
    url = "https://api.ebay.com/buy/browse/v1/item_summary/search"
    
    headers = {"Authorization": f"Bearer {access_token}"}
    params = {"q": keyword, "limit": limit}
    
    response = requests.get(url, headers=headers, params=params)
    response.raise_for_status()
    print("   SUCCESS! Data received from the Browse API.")
    return response.json()

# --- Main Program ---
try:
    token = get_browse_api_token()
    
    product_to_research = "Macbook Air M1"
    
    data = find_active_items(token, product_to_research, limit=200)
    
    # Process the results from the Browse API
    if data.get('itemSummaries'):
        items_list = []
        for item in data['itemSummaries']:
            item_details = {
                'title': item.get('title'),
                'price': float(item.get('price', {}).get('value', 0)),
                'currency': item.get('price', {}).get('currency'),
                'condition': item.get('condition'),
                'item_url': item.get('itemWebUrl')
            }
            items_list.append(item_details)
            
        df = pd.DataFrame(items_list)
        print(f"\n3. Created a DataFrame with {len(df)} active listings.")

        # --- Your Project Analysis Starts Here ---
        print("\n--- Current Market Analysis ---")
        
        # Remove listings with price 0 (if any)
        df = df[df['price'] > 0]
        
        average_price = df['price'].mean()
        print(f"Current Average Price: ${average_price:.2f}")

        print("\nListings by Condition:")
        print(df['condition'].value_counts())
        
        # Display the DataFrame in your notebook
        # In a new cell you can type 'df.head()' to see it.
        
    else:
        print("\nNo active listings found for this search.")
        df = pd.DataFrame()

except Exception as e:
    print("\n--- AN ERROR OCCURRED ---")
    print(e)

1. Getting the correct access token...
   SUCCESS! Token obtained.

2. Searching for ACTIVE listings for: 'Macbook Air M1'...
   SUCCESS! Data received from the Browse API.

3. Created a DataFrame with 200 active listings.

--- Current Market Analysis ---
Current Average Price: $422.38

Listings by Condition:
condition
Used                        120
Very Good - Refurbished      25
Good - Refurbished           23
Excellent - Refurbished      17
New                           9
Open box                      3
For parts or not working      3
Name: count, dtype: int64


In [9]:
import pandas as pd
import re # We need the regular expressions library for text processing

# We already have the functions and token from the previous steps.
# If your token has expired, re-run the cell that calls get_browse_api_token().

# 1. DEFINE A BROAD KEYWORD FOR THE CATEGORY
broad_keyword = "Macbook"

# 2. GET A LARGE SAMPLE OF DATA (up to 1000 listings)
# We re-use our powerful function from before.
macbook_listings_raw = find_all_active_items(token, broad_keyword)

# 3. CONVERT TO A DATAFRAME
df_discovery = pd.DataFrame(macbook_listings_raw)
print(f"Discovery phase found {len(df_discovery)} total listings for '{broad_keyword}'.")

# 4. EXTRACT MODEL NAMES FROM TITLES
def extract_macbook_model(title):
    # This regular expression looks for patterns like "Macbook Pro M1", "Macbook Air 13-inch", etc.
    # It's not perfect, but it's a great start.
    match = re.search(r"(MacBook\s(Pro|Air)\s[A-Z0-9\s\.\-inch]*)", title, re.IGNORECASE)
    if match:
        # Clean up the found text
        return match.group(1).strip()
    return None

df_discovery['extracted_model'] = df_discovery['title'].apply(extract_macbook_model)

# 5. COUNT AND DISPLAY THE MOST COMMON MODELS FOUND
# This is the most valuable output of our discovery phase.
model_counts = df_discovery['extracted_model'].value_counts()

print("\n--- Discovered MacBook Models (Top 20) ---")
print("This is the list you can use to build your final keyword list.")
print(model_counts.head(20))

NameError: name 'find_all_active_items' is not defined

In [10]:
# --- Cell 1: Setup ---

import requests
import base64
import pandas as pd
import json
import time
import re 

# --- Your Production Keys ---


print("Setup Complete. Libraries and credentials are loaded.")

Setup Complete. Libraries and credentials are loaded.


In [11]:
# --- Cell 2: Function Definitions ---

def get_browse_api_token():
    """Gets the simple token needed for the Browse API."""
    print("Getting access token...")
    url = "https://api.ebay.com/identity/v1/oauth2/token" 
    headers = {"Content-Type": "application/x-www-form-urlencoded", "Authorization": "Basic " + base64.b64encode(f"{CLIENT_ID_PRODUCTION}:{CLIENT_SECRET_PRODUCTION}".encode()).decode()}
    body = {"grant_type": "client_credentials", "scope": "https://api.ebay.com/oauth/api_scope"}
    response = requests.post(url, headers=headers, data=body)
    response.raise_for_status() 
    print("   SUCCESS! Token obtained.")
    return response.json()["access_token"]

def find_all_active_items(access_token, keyword):
    """Finds all active listings for a keyword, handling pagination automatically."""
    print(f"\nSearching for ALL active listings for broad keyword: '{keyword}'...")
    all_items = []
    endpoint_url = "https://api.ebay.com/buy/browse/v1/item_summary/search"
    headers = {"Authorization": f"Bearer {access_token}"}
    params = {"q": keyword, "limit": 200, "sort": "price"} 

    max_pages = 5 
    for page_num in range(max_pages):
        if not endpoint_url:
            break
        print(f"   Fetching discovery page {page_num + 1}/{max_pages}...")
        response = requests.get(endpoint_url, headers=headers, params=params)
        if response.status_code != 200:
            break
        data = response.json()
        if data.get('itemSummaries'):
            all_items.extend(data['itemSummaries'])
        endpoint_url = data.get("next")
        params = {}
        time.sleep(0.5)
    print(f"--- Finished discovery for '{keyword}'. Found {len(all_items)} sample listings. ---")
    return all_items

print("Functions are now defined and ready to be used.")

Functions are now defined and ready to be used.


In [12]:
token = get_browse_api_token()

Getting access token...
   SUCCESS! Token obtained.


In [13]:
# --- Cell 4: The Main Discovery Loop ---

# This dictionary holds the broad search term and the specific text pattern for each category.
category_discovery_config = {
    "MacBook": r"(MacBook\s(?:Pro|Air)[\s\w\d\.\-inch]*)",
    "iPhone": r"(iPhone\s(?:SE|\d{1,2})\s?(?:Pro|Max|Mini|Plus)?)",
    "Apple Watch": r"(Apple\sWatch\s(?:Series\s\d|Ultra|SE))",
    "iPad": r"(iPad\s(?:Pro|Air|Mini)?[\s\d\w\.\-thgeninch]*)",
    "AirPods": r"(AirPods\s(?:Pro|Max|\d.. Gen|Pro\s\d.. Gen))"
}

all_discovered_models = {}

for category, pattern in category_discovery_config.items():
    raw_listings = find_all_active_items(token, category)
    if not raw_listings:
        print(f"No listings found for {category}, skipping.")
        continue
    
    df_discovery = pd.DataFrame(raw_listings)

    def extract_model(title, regex_pattern):
        if not isinstance(title, str): return None
        match = re.search(regex_pattern, title, re.IGNORECASE)
        if match: return " ".join(match.group(1).split())
        return None

    df_discovery['extracted_model'] = df_discovery['title'].apply(lambda title: extract_model(title, pattern))
    model_counts = df_discovery['extracted_model'].value_counts()
    all_discovered_models[category] = model_counts.head(15)

print("\n\nDiscovery Phase Complete! Results are stored.")


Searching for ALL active listings for broad keyword: 'MacBook'...
   Fetching discovery page 1/5...
   Fetching discovery page 2/5...
   Fetching discovery page 3/5...
   Fetching discovery page 4/5...
   Fetching discovery page 5/5...
--- Finished discovery for 'MacBook'. Found 1000 sample listings. ---

Searching for ALL active listings for broad keyword: 'iPhone'...
   Fetching discovery page 1/5...
   Fetching discovery page 2/5...
   Fetching discovery page 3/5...
   Fetching discovery page 4/5...
   Fetching discovery page 5/5...
--- Finished discovery for 'iPhone'. Found 1000 sample listings. ---

Searching for ALL active listings for broad keyword: 'Apple Watch'...
   Fetching discovery page 1/5...
   Fetching discovery page 2/5...
   Fetching discovery page 3/5...
   Fetching discovery page 4/5...
   Fetching discovery page 5/5...
--- Finished discovery for 'Apple Watch'. Found 1000 sample listings. ---

Searching for ALL active listings for broad keyword: 'iPad'...
   Fetchi

In [14]:
# --- Cell 5: Display the Results ---

print("=======================================================")
print("          DISCOVERY PHASE RESULTS")
print("=======================================================")

for category, models in all_discovered_models.items():
    print(f"\n--- Top Discovered Models for: {category} ---")
    if models.empty:
        print("   (No models were successfully extracted for this category)")
    else:
        print(models)
    print("-" * (30 + len(category)))

          DISCOVERY PHASE RESULTS

--- Top Discovered Models for: MacBook ---
extracted_model
MacBook Pro 13            66
MacBook Pro 15            28
MacBook Air 13            25
MacBook Air 11            17
MacBook Pro Retina 13     14
Macbook Pro Retina 13     12
MacBook Air Pro Mac 11    11
MacBook Pro               11
Macbook Pro Air Mac        9
MacBook Pro Retina 15      9
Macbook Air                8
MacBook Pro Unibody 13     8
Macbook Pro 15             7
Macbook Air 13             7
MACBOOK PRO 13             6
Name: count, dtype: int64
-------------------------------------

--- Top Discovered Models for: iPhone ---
extracted_model
iPhone 14         152
iPhone 15         127
iPhone 16          58
iPhone 13          37
iPhone 6           33
iPhone 11          30
iPhone 12          29
iPhone 7           27
iPhone 5           24
iphone 14          21
iPhone 16 Pro      16
iPhone 12 Mini     15
iPhone 11 Pro      11
iPhone 13 Pro      11
iPhone 4           10
Name: count, dtype

In [15]:
# --- Cell 1: The Complete Discovery Engine ---

import requests
import base64
import pandas as pd
import json
import time
import re

# --- Your Production Keys ---
CLIENT_ID_PRODUCTION = "Kamalpre-retailpr-PRD-f8e8dd193-b0972a73"
CLIENT_SECRET_PRODUCTION = "PRD-8e8dd193d73f-b8d1-4bad-a5ca-ec24"

# --- API Functions ---
def get_browse_api_token():
    print("1. Getting access token...")
    url = "https://api.ebay.com/identity/v1/oauth2/token" 
    headers = {"Content-Type": "application/x-www-form-urlencoded", "Authorization": "Basic " + base64.b64encode(f"{CLIENT_ID_PRODUCTION}:{CLIENT_SECRET_PRODUCTION}".encode()).decode()}
    body = {"grant_type": "client_credentials", "scope": "https://api.ebay.com/oauth/api_scope"}
    response = requests.post(url, headers=headers, data=body)
    response.raise_for_status() 
    print("   SUCCESS! Token obtained.")
    return response.json()["access_token"]

def find_all_active_items(access_token, keyword):
    print(f"\nSearching for ALL active listings for broad keyword: '{keyword}'...")
    all_items = []
    endpoint_url = "https://api.ebay.com/buy/browse/v1/item_summary/search"
    headers = {"Authorization": f"Bearer {access_token}"}
    params = {"q": keyword, "limit": 200, "sort": "price"}
    max_pages = 5 
    for page_num in range(max_pages):
        if not endpoint_url: break
        print(f"   Fetching discovery page {page_num + 1}/{max_pages}...")
        response = requests.get(endpoint_url, headers=headers, params=params)
        if response.status_code != 200: break
        data = response.json()
        if data.get('itemSummaries'): all_items.extend(data['itemSummaries'])
        endpoint_url = data.get("next")
        params = {}
        time.sleep(0.5)
    print(f"--- Finished discovery for '{keyword}'. Found {len(all_items)} sample listings. ---")
    return all_items

# --- DISCOVERY CONFIGURATION AND EXECUTION ---
category_discovery_config = {
    "MacBook": r"(MacBook\s(?:Pro|Air)[\s\w\d\.\-inch]*)",
    "iPhone": r"(iPhone\s(?:SE|\d{1,2})\s?(?:Pro|Max|Mini|Plus)?)",
    "Apple Watch": r"(Apple\sWatch\s(?:Series\s\d|Ultra|SE))",
    "iPad": r"(iPad\s(?:Pro|Air|Mini)?[\s\d\w\.\-thgeninch]*)",
    "AirPods": r"(AirPods\s(?:Pro|Max|\d.. Gen|Pro\s\d.. Gen))"
}

print("Starting Discovery Phase...")
token = get_browse_api_token()
all_discovered_models = {}

for category, pattern in category_discovery_config.items():
    raw_listings = find_all_active_items(token, category)
    if not raw_listings:
        print(f"No listings found for {category}, skipping.")
        continue
    df_discovery = pd.DataFrame(raw_listings)
    def extract_model(title, regex_pattern):
        if not isinstance(title, str): return None
        match = re.search(regex_pattern, title, re.IGNORECASE)
        if match: return " ".join(match.group(1).split())
        return None
    df_discovery['extracted_model'] = df_discovery['title'].apply(lambda title: extract_model(title, pattern))
    model_counts = df_discovery['extracted_model'].value_counts()
    all_discovered_models[category] = model_counts

print("\n\n=======================================================")
print("          DISCOVERY PHASE COMPLETE!")
print("The 'all_discovered_models' variable is now ready.")
print("=======================================================")

Starting Discovery Phase...
1. Getting access token...
   SUCCESS! Token obtained.

Searching for ALL active listings for broad keyword: 'MacBook'...
   Fetching discovery page 1/5...
   Fetching discovery page 2/5...
   Fetching discovery page 3/5...
   Fetching discovery page 4/5...
   Fetching discovery page 5/5...
--- Finished discovery for 'MacBook'. Found 1000 sample listings. ---

Searching for ALL active listings for broad keyword: 'iPhone'...
   Fetching discovery page 1/5...
   Fetching discovery page 2/5...
   Fetching discovery page 3/5...
   Fetching discovery page 4/5...
   Fetching discovery page 5/5...
--- Finished discovery for 'iPhone'. Found 1000 sample listings. ---

Searching for ALL active listings for broad keyword: 'Apple Watch'...
   Fetching discovery page 1/5...
   Fetching discovery page 2/5...
   Fetching discovery page 3/5...
   Fetching discovery page 4/5...
   Fetching discovery page 5/5...
--- Finished discovery for 'Apple Watch'. Found 1000 sample list

In [16]:
# --- Cell 2: Organize Discovery Results into a DataFrame ---

# This list will hold temporary DataFrames, one for each category
data_to_combine = []

print("Organizing the discovered data into a single table...")

# Loop through the dictionary that was created in the previous cell
for category, models_series in all_discovered_models.items():
    if not models_series.empty:
        # Convert the Pandas Series for the current category into a DataFrame
        temp_df = models_series.reset_index()
        
        # Rename the columns to be clear and useful
        temp_df.columns = ['discovered_model', 'listing_count']
        
        # Add the 'category' column so we know where these models came from
        temp_df['category'] = category
        
        # Add this newly created DataFrame to our list
        data_to_combine.append(temp_df)

# Combine all the temporary DataFrames into one master DataFrame
if data_to_combine:
    df_discovered_summary = pd.concat(data_to_combine, ignore_index=True)
    
    # Reorder columns for better readability
    df_discovered_summary = df_discovered_summary[['category', 'discovered_model', 'listing_count']]
    
    print("\nSUCCESS! Your master DataFrame of discovered models has been created.")
    
else:
    print("\nNo models were discovered. The DataFrame is empty.")
    df_discovered_summary = pd.DataFrame()

Organizing the discovered data into a single table...

SUCCESS! Your master DataFrame of discovered models has been created.


In [17]:
# --- Cell 3: Verify and Explore the Master DataFrame ---

if not df_discovered_summary.empty:
    print("--- DataFrame Information ---")
    # Get the structure of your table: total rows, columns, etc.
    df_discovered_summary.info()

    print("\n\n--- First 10 Rows of Your Dataset ---")
    # Look at the beginning of your data
    display(df_discovered_summary.head(10))

    print("\n\n--- Last 10 Rows of Your Dataset ---")
    # Look at the end to see data from other categories
    display(df_discovered_summary.tail(10))

    print("\n\n--- Total Discovered Models per Category ---")
    # This shows how many unique models you found for each category
    print(df_discovered_summary['category'].value_counts())
else:
    print("DataFrame is empty. Nothing to display.")

--- DataFrame Information ---
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 701 entries, 0 to 700
Data columns (total 3 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   category          701 non-null    object
 1   discovered_model  701 non-null    object
 2   listing_count     701 non-null    int64 
dtypes: int64(1), object(2)
memory usage: 16.6+ KB


--- First 10 Rows of Your Dataset ---


category        discovered_model  listing_count
0  MacBook          MacBook Pro 13             66
1  MacBook          MacBook Pro 15             28
2  MacBook          MacBook Air 13             25
3  MacBook          MacBook Air 11             17
4  MacBook   MacBook Pro Retina 13             14
5  MacBook   Macbook Pro Retina 13             12
6  MacBook  MacBook Air Pro Mac 11             11
7  MacBook             MacBook Pro             11
8  MacBook     Macbook Pro Air Mac              9
9  MacBook   MacBook Pro Retina 15              9



--- Last 10 Rows of Your Dataset ---


category discovered_model  listing_count
691  AirPods  Airpods 4th Gen              2
692  AirPods  airpods 1st gen              1
693  AirPods  airpods 2nd gen              1
694  AirPods      Airpods pro              1
695  AirPods  AIRPODS 2ND GEN              1
696  AirPods  Airpods 3Rd Gen              1
697  AirPods  Airpods 2/1 Gen              1
698  AirPods  Airpods 1st Gen              1
699  AirPods      AirPods Max              1
700  AirPods  AirPods 2st Gen              1



--- Total Discovered Models per Category ---
category
iPad           334
MacBook        257
iPhone          68
AirPods         26
Apple Watch     16
Name: count, dtype: int64


In [21]:
# --- Cell 1: Setup - Imports, Credentials, and Functions ---

import requests
import base64
import pandas as pd
import json
import time

# --- Your Production Keys ---
CLIENT_ID_PRODUCTION = "Kamalpre-retailpr-PRD-f8e8dd193-b0972a73"
CLIENT_SECRET_PRODUCTION = "PRD-8e8dd193d73f-b8d1-4bad-a5ca-ec24"

# --- Function Definitions ---
def get_browse_api_token():
    """Gets the simple token needed for the Browse API."""
    print("1. Getting access token...")
    url = "https://api.ebay.com/identity/v1/oauth2/token" 
    headers = {"Content-Type": "application/x-www-form-urlencoded", "Authorization": "Basic " + base64.b64encode(f"{CLIENT_ID_PRODUCTION}:{CLIENT_SECRET_PRODUCTION}".encode()).decode()}
    body = {"grant_type": "client_credentials", "scope": "https://api.ebay.com/oauth/api_scope"}
    response = requests.post(url, headers=headers, data=body)
    response.raise_for_status() 
    print("   SUCCESS! Token obtained.")
    return response.json()["access_token"]

def find_all_active_items(access_token, keyword):
    """Finds all active listings for a keyword, handling pagination automatically."""
    print(f"\nSearching for ALL active listings for broad category: '{keyword}'...")
    all_items = []
    endpoint_url = "https://api.ebay.com/buy/browse/v1/item_summary/search"
    headers = {"Authorization": f"Bearer {access_token}"}
    params = {"q": keyword, "limit": 200}

    max_pages = 5 # We'll fetch up to 1000 listings per category
    for page_num in range(max_pages):
        if not endpoint_url: break
        print(f"   Fetching page {page_num + 1}/{max_pages}...")
        response = requests.get(endpoint_url, headers=headers, params=params)
        if response.status_code != 200: break
        data = response.json()
        if data.get('itemSummaries'):
            all_items.extend(data['itemSummaries'])
        endpoint_url = data.get("next")
        params = {}
        time.sleep(0.5)
    print(f"--- Finished searching for '{keyword}'. Found {len(all_items)} listings. ---")
    return all_items

# This print statement confirms that the cell has run successfully.
print("Setup Complete. Functions are ready.")

Setup Complete. Functions are ready.


In [22]:
# --- Cell 2: Collect All Listings from All Broad Categories (Corrected) ---

# Define the broad categories you want to collect data for.
categories_to_fetch = [
    "MacBook",
    "iPhone",
    "Apple Watch",
    "iPad",
    "AirPods"
]

# Get a fresh token for this session of data collection.
print("Starting the full data collection process...")
try:
    token = get_browse_api_token()

    # This list will hold every single raw listing from all categories.
    all_raw_listings = []

    # Loop through each category you defined above.
    for category in categories_to_fetch:
        # Use the function from Cell 1 to get the data for the current category.
        raw_listings_for_category = find_all_active_items(token, category)
        
        # This is a critical step: Add the category name to each item before storing it.
        for item in raw_listings_for_category:
            item['category_searched'] = category # This creates our new column.
    
        # Add all the newly tagged listings to our one master list.
        all_raw_listings.extend(raw_listings_for_category)

    # A final confirmation message when the loop is done.
    print("\n\n=======================================================")
    print(f"DATA COLLECTION COMPLETE! Total raw listings collected: {len(all_raw_listings)}")
    print("The variable 'all_raw_listings' is now ready for the next step.")
    print("=======================================================")

except Exception as e:
    print(f"\n--- AN ERROR OCCURRED ---")
    print(f"Error details: {e}")

Starting the full data collection process...
1. Getting access token...
   SUCCESS! Token obtained.

Searching for ALL active listings for broad category: 'MacBook'...
   Fetching page 1/5...
   Fetching page 2/5...
   Fetching page 3/5...
   Fetching page 4/5...
   Fetching page 5/5...
--- Finished searching for 'MacBook'. Found 1000 listings. ---

Searching for ALL active listings for broad category: 'iPhone'...
   Fetching page 1/5...
   Fetching page 2/5...
   Fetching page 3/5...
   Fetching page 4/5...
   Fetching page 5/5...
--- Finished searching for 'iPhone'. Found 1000 listings. ---

Searching for ALL active listings for broad category: 'Apple Watch'...
   Fetching page 1/5...
   Fetching page 2/5...
   Fetching page 3/5...
   Fetching page 4/5...
   Fetching page 5/5...
--- Finished searching for 'Apple Watch'. Found 1000 listings. ---

Searching for ALL active listings for broad category: 'iPad'...
   Fetching page 1/5...
   Fetching page 2/5...
   Fetching page 3/5...
   F

In [25]:
# --- Cell 2: Collect All Listings (Corrected for Indentation) ---

try:
    # Define the broad categories you want to collect data for.
    categories_to_fetch = [
        "MacBook",
        "iPhone",
        "Apple Watch",
        "iPad",
        "AirPods"
    ]

    # Get a fresh token for this session of data collection.
    print("Starting the full data collection process...")
    token = get_browse_api_token()

    # This list will hold every single raw listing from all categories.
    all_raw_listings = []

    # Loop through each category you defined above.
    for category in categories_to_fetch:
        # Use the function from Cell 1 to get the data for the current category.
        raw_listings_for_category = find_all_active_items(token, category)
        
        # This is a critical step: Add the category name to each item before storing it.
        for item in raw_listings_for_category:
            item['category_searched'] = category # This creates our new column.
    
        # Add all the newly tagged listings to our one master list.
        all_raw_listings.extend(raw_listings_for_category)

    # A final confirmation message when the loop is done.
    print("\n\n=======================================================")
    print(f"DATA COLLECTION COMPLETE! Total raw listings collected: {len(all_raw_listings)}")
    print("The variable 'all_raw_listings' is now ready for the next step.")
    print("=======================================================")

except Exception as e:
    print(f"\n--- AN ERROR OCCURRED ---")
    print(f"Error details: {e}")

Starting the full data collection process...
1. Getting access token...
   SUCCESS! Token obtained.

Searching for ALL active listings for broad category: 'MacBook'...
   Fetching page 1/5...
   Fetching page 2/5...
   Fetching page 3/5...
   Fetching page 4/5...
   Fetching page 5/5...
--- Finished searching for 'MacBook'. Found 1000 listings. ---

Searching for ALL active listings for broad category: 'iPhone'...
   Fetching page 1/5...
   Fetching page 2/5...
   Fetching page 3/5...
   Fetching page 4/5...
   Fetching page 5/5...
--- Finished searching for 'iPhone'. Found 1000 listings. ---

Searching for ALL active listings for broad category: 'Apple Watch'...
   Fetching page 1/5...
   Fetching page 2/5...
   Fetching page 3/5...
   Fetching page 4/5...
   Fetching page 5/5...
--- Finished searching for 'Apple Watch'. Found 1000 listings. ---

Searching for ALL active listings for broad category: 'iPad'...
   Fetching page 1/5...
   Fetching page 2/5...
   Fetching page 3/5...
   F

In [26]:
# --- Cell 3: Create, Organize, and Save the Master DataFrame (The Correct Version) ---

# First, we check if the 'all_raw_listings' variable exists and has data in it.
# This prevents errors if the previous cell failed for any reason.
if 'all_raw_listings' in locals() and all_raw_listings:
    
    # This print statement confirms the process is starting.
    print("Organizing all collected listings into a single DataFrame...")

    # We will create a new, clean list to hold our structured data.
    final_data_list = []

    # Now, we loop through every single raw listing we collected.
    # The .get() method is used to safely access data that might sometimes be missing from a listing.
    for item in all_raw_listings:
        final_data_list.append({
            'category': item.get('category_searched'),
            'title': item.get('title'),
            'price': float(item.get('price', {}).get('value', 0)),
            'currency': item.get('price', {}).get('currency'),
            'condition': item.get('condition'),
            'seller_username': item.get('seller', {}).get('username'),
            'shipping_cost': float(item.get('shippingOptions', [{}])[0].get('shippingCost', {}).get('value', 0)),
            'item_id': item.get('itemId'),
            'image_url': item.get('image', {}).get('imageUrl'),
            'item_url': item.get('itemWebUrl')
        })

    # Create the final, master DataFrame from our list of processed data.
    df_raw_market_data = pd.DataFrame(final_data_list)

    # Print a confirmation message with the size of the new DataFrame.
    print(f"\nMaster DataFrame created successfully with {len(df_raw_market_data)} rows and {len(df_raw_market_data.columns)} columns.")

    # --- Save the Raw DataFrame ---
    # This is a crucial step so you don't have to run the API calls again.
    file_name = "full_raw_apple_market_data.csv"
    df_raw_market_data.to_csv(file_name, index=False)
    print(f"\nSUCCESS! Your complete, raw dataset has been saved to '{file_name}'")

    # --- Display a Sample of Your New DataFrame ---
    # This shows you the final result of your data collection.
    print("\nHere is a sample of your full, raw dataset:")
    display(df_raw_market_data.head())
    
else:
    # This message will appear if something went wrong in the previous cell.
    print("\nERROR: The 'all_raw_listings' list is empty. No DataFrame was created. Please re-run Cell 2 to collect the data.")

Organizing all collected listings into a single DataFrame...

Master DataFrame created successfully with 5000 rows and 10 columns.

SUCCESS! Your complete, raw dataset has been saved to 'full_raw_apple_market_data.csv'

Here is a sample of your full, raw dataset:


category                                              title    price  \
0  MacBook  13 Apple Macbook Pro Core i5 3.5GHz Turbo 256G...   419.00   
1  MacBook  Apple MacBook 13" Laptop READY TO USE w/ macOS...   135.00   
2  MacBook  LOADED!! Apple MacBook Pro Retina 15" i7 + Tou...   745.75   
3  MacBook  Apple MacBook 13" Laptop READY TO USE w/ macOS...    77.77   
4  MacBook  Apple 2024 MacBook Pro 14-inch M4 Chip 16GB RA...  1299.00   

  currency condition seller_username  shipping_cost  \
0      USD      Used   payless4apple            0.0   
1      USD      Used         laptops            0.0   
2      USD      Used         jre3533            0.0   
3      USD      Used         laptops            0.0   
4      USD  Open box    ipowerresale            0.0   

                        item_id  \
0             v1|235087307033|0   
1  v1|256929065877|557519127056   
2             v1|256361196775|0   
3  v1|267299359229|567082603226   
4             v1|256793837833|0   

                                           image_url  \
0  https://i.ebayimg.com/images/g/DmEAAOSwGNRjK0Y...   
1  https://i.ebayimg.com/images/g/K88AAOSw0FRfrrp...   
2  https://i.ebayimg.com/images/g/lDcAAOSwY-JlkhD...   
3  https://i.ebayimg.com/images/g/K88AAOSw0FRfrrp...   
4  https://i.ebayimg.com/images/g/60gAAOSw8Ftnk-9...   

                                            item_url  
0  https://www.ebay.com/itm/235087307033?_skw=Mac...  
1  https://www.ebay.com/itm/256929065877?_skw=Mac...  
2  https://www.ebay.com/itm/256361196775?_skw=Mac...  
3  https://www.ebay.com/itm/267299359229?_skw=Mac...  
4  https://www.ebay.com/itm/256793837833?_skw=Mac...

In [27]:
# --- To see all the rows of your DataFrame ---

# 1. Temporarily change the display setting to show an unlimited number of rows.
pd.set_option('display.max_rows', None)

# 2. Display your DataFrame. All rows will now be visible.
display(df_raw_market_data)

# 3. (Optional but recommended) Reset the display setting back to default.
pd.reset_option('display.max_rows')

category                                              title    price  \
0         MacBook  13 Apple Macbook Pro Core i5 3.5GHz Turbo 256G...   419.00   
1         MacBook  Apple MacBook 13" Laptop READY TO USE w/ macOS...   135.00   
2         MacBook  LOADED!! Apple MacBook Pro Retina 15" i7 + Tou...   745.75   
3         MacBook  Apple MacBook 13" Laptop READY TO USE w/ macOS...    77.77   
4         MacBook  Apple 2024 MacBook Pro 14-inch M4 Chip 16GB RA...  1299.00   
5         MacBook  Apple MacBook Pro 13" Retina, Touch Bar, Intel...   279.00   
6         MacBook  Apple MacBook Pro 15.4-Inch Intel Core i9, 32G...   459.00   
7         MacBook  Apple MacBook Air 13.6" (256GB SSD, M2, 8GB) L...   536.00   
8         MacBook  2024 Apple MacBook Air 13-inch M3 Chip 16GB RA...   749.00   
9         MacBook  2019 Apple MacBook Pro 13" i7 2.8GHz/16GB/256G...   330.00   
10        MacBook  MacBook Air 15-inch 2024 M3 / 16GB RAM / 512GB...   969.00   
11        MacBook  Apple Macbook Pro 13" Laptop | UPGRADED i5 16G...   149.00   
12        MacBook  Apple 14.2 MacBook Pro M1 16GB RAM 512GB SSD S...   709.95   
13        MacBook  Apple MacBook Pro 15" (Intel Core i9 2.3GHz, 1...   475.00   
14        MacBook  Apple MacBook Air 13.3" Intel Core i3 1.10 GHz...   347.99   
15        MacBook  Apple MacBook Pro 15" A1398 i7-4870HQ 2.50Ghz ...   125.00   
16        MacBook  Apple MacBook Air 13" M4 chip 16GB RAM 256GB S...   799.00   
17        MacBook  2024 Apple MacBook Air 15-inch M3 Chip 16GB RA...   849.00   
18        MacBook  Apple MacBook Air 13.3 (2015)" - i5-5250U - 8G...   119.99   
19        MacBook  2017 Apple MacBook Air 13" Dual Core i5 8GB 12...   139.00   
20        MacBook  Apple MacBook Pro Mid 2015 15" Retina 2.50Ghz ...   149.95   
21        MacBook  Apple MacBook Pro RETINA 15" Quad Core i7 16GB...   229.00   
22        MacBook  Apple A2251 Macbook Pro 13" 2020 Intel i5-1038...   309.99   
23        MacBook  Apple MacBook Air (13-inch, M3, 2024) 24GB RAM...  1089.00   
24        MacBook  Apple MacBook Air Core i5 1.8GHz 8GB RAM 128GB...   179.99   
25        MacBook  Apple Macbook Air 2013 A1465 11" I5 1.3GHz 4GB...    74.99   
26        MacBook  Apple MacBook Pro 13 M1 8-Core 16GB 512GB Gray...   498.99   
27        MacBook  Apple Macbook Air A1466 13.3 i5-4260U 1.4 Ghz ...    59.99   
28        MacBook  Apple MacBook Air  - 13'' Laptop - 8GB RAM - 1...   189.99   
29        MacBook  Apple MacBook Pro 15" 1TB SSD 16GB i7 3.40Ghz ...   389.06   
30        MacBook  Apple MacBook Air Core i7 2.2GHz 8GB RAM 256GB...   244.99   
31        MacBook  2018 Apple MacBook Pro 15" Touchbar (512GB SSD...   299.99   
32        MacBook  Apple MacBook Air M3 15.3in 8-CoreCPU 10-CoreG...   790.00   
33        MacBook  Apple Macbook Pro 13" Laptop -i5 8GB RAM 128GB...    99.00   
34        MacBook  2019 Apple MacBook Pro 13.3" i5 1.4GHz 8GB RAM...   249.99   
35        MacBook  2015 Apple MacBook Pro 13" Retina/ 2.7 Core i5...   175.00   
36        MacBook  2022 OSX | 2017-2018 MacBook Pro 15" Touch Bar...   500.00   
37        MacBook  APPLE MACBOOK AIR 13 INCH LAPTOP | 8GB RAM | 1...   319.00   
38        MacBook  Apple MacBook Pro 15" 2015/2014 A1398 i7-4770H...   124.00   
39        MacBook  Apple MacBook Pro 13" Laptop | 1TB SSD | 16GB ...   250.26   
40        MacBook  Apple MacBook Air Core i5 1.6GHz 8GB RAM 256GB...   334.99   
41        MacBook  Apple Macbook 13" (No TouchBar, 2017) - i5 7th...   199.99   
42        MacBook  2022 Apple M2 MacBook Pro 13.3" 16GB/512GB SSD...   809.00   
43        MacBook  Apple MacBook Air with M1 Chip 13-inch 16GB 51...   589.00   
44        MacBook  Apple MacBook Pro 15.4-inch, Touch Bar, Core i...   299.00   
45        MacBook  Apple Macbook Air 13" Laptop - i5 8GB RAM 256G...   170.05   
46        MacBook  Apple MacBook Pro A1990 15 inch i7 SEQUOIA Tou...   525.00   
47        MacBook  MAXED!! Apple MacBook Air Retina 13" + LOADED!...   631.75   
48        MacBook  Apple MacBook Pro 15"